In [2]:
"""
Data Preprocessing
"""

import os
import re
import pandas as pd

# read train data
file_dir = '/Users/dnhb/PycharmProjects/SML_Ass1'
file_name = "train.txt"

def parse(data:list)->list: 
    # Python Notation: https://www.python.org/dev/peps/pep-3107/
    """
    Prase each line of the data
    Return a nested list, such as [[id1, id2, id2,...],...]
    """
    parsed_data = []
    for line in data:
        # remove \n at the end of each line
        line = re.sub(r"(?<=\d)\n", "", line)
        # split IDs by \t
        pattern = re.compile("(?<=\d)\t(?=\d)")
        line = re.split(pattern, line)
        parsed_data.append(line)
    return parsed_data

with open(os.path.join(file_dir, file_name)) as f:
    train_set = f.readlines()
    train_set = parse(train_set)
    
# read test data
test_name = "test-public.txt"
with open(os.path.join(file_dir, test_name)) as f:
    test_set = f.readlines()
    test_set = parse(test_set)
    test_set.pop(0)

# turn ID into int
for i in range(0, len(test_set)):
    test_set[i][0] = int(test_set[i][0])
    
print("Data has been read.")

Data has been read.


In [3]:
"""
Sigma Data For Similarity
"""

from collections import defaultdict

train_dic = {}
for item in train_set:
    train_dic[item[0]] = item[1:]

# construct SigmaOut dic for each node
SigmaOut = defaultdict(set)

def getSigmaOut(node:str, graph:dict) -> set:
    SigmaOut = set()
    try:
        for item in graph[node]:
            SigmaOut.add(item)
        return SigmaOut
    except:
        return SigmaOut

for kw in train_dic:
    SigmaOut[kw] = getSigmaOut(kw, train_dic)
    
print("SigmaOut done.\n")

# construct SigmaIn dic for each node
SigmaIn = defaultdict(set)

for kw in train_dic:
    for followee in train_dic[kw]:
        if SigmaIn[followee]:
            SigmaIn[followee].add(kw)
        else:
            SigmaIn[followee] = {kw}

def getSigma(node:str) -> set:
    return SigmaIn[node].union(SigmaOut[node])

print("SigmaIn done.")

SigmaOut done.

SigmaIn done.


In [4]:
"""
Similarity Functions
"""

import math

    
def adar1(a:str, b:str) -> float:
    score = 0
    SigmaA = getSigma(a)
    SigmaB = getSigma(b) 
    SigmaV = SigmaA.intersection(SigmaB)
    if SigmaV:
        for v in SigmaV:
            if getSigma(v) and len(getSigma(v)) != 1:
                   score += (1/math.log(len(getSigma(v))))
            else:
                   pass
        return score
    else:
        return 0

def adar2(a:str, b:str) -> float:
    score = 0
    SigmaOutA = SigmaOut[a]
    if SigmaOutA:
        for node in SigmaOutA:
            score += adar1(b, node)
        return float(score/len(SigmaOutA))
    else:
        return 0
    
def adar3(a:str, b:str) -> float:
    score = 0
    SigmaInB = SigmaIn[b]
    if SigmaInB:
        for node in SigmaInB:
            score += adar1(a, node)
        return float(score/len(SigmaInB))
    else:
        return 0
  
def jaccard1(a:str, b:str) -> float:
    SigmaA = getSigma(a)
    SigmaB = getSigma(b)
    return float(len(SigmaA.intersection(SigmaB)) / len(SigmaA.union(SigmaB)))

def jaccard2(a:str, b:str) -> float:
    score = 0
    SigmaOutA = SigmaOut[a]
    if SigmaOutA:
        for node in SigmaOutA:
            score += jaccard1(b, node)
        return float(score/len(SigmaOutA))
    else:
        return 0

def jaccard3(a:str, b:str) -> float:
    score = 0
    SigmaInB = SigmaIn[b]
    if SigmaInB:
        for node in SigmaInB:
            score += jaccard1(a, node)
        return float(score/len(SigmaInB))
    else:
        return 0
    
def cosine1(a:str, b:str) -> float:
    SigmaA = getSigma(a)
    SigmaB = getSigma(b)
    return float(len(SigmaA.intersection(SigmaB)) / (len(SigmaA)*len(SigmaB)))


def cosine2(a:str, b:str) -> float:
    score = 0
    SigmaOutA = SigmaOut[a]
    if SigmaOutA:
        for node in SigmaOutA:
            score += cosine1(b, node)
        return float(score/len(SigmaOutA))
    else:
        return 0

def cosine3(a:str, b:str) -> float:
    score = 0
    SigmaInB = SigmaIn[b]
    if SigmaInB:
        for node in SigmaInB:
            score += cosine1(a, node)
        return float(score/len(SigmaInB))
    else:
        return 0

def common_neighbors1(a: str, b: str) -> float:
    SigmaA = getSigma(a)
    SigmaB = getSigma(b)
    return len(SigmaA.intersection(SigmaB))

def common_neighbors2(a: str, b: str) -> float:
     score = 0
     SigmaOutA = SigmaOut[a]
     if SigmaOutA:
         for node in SigmaOutA:
             score += common_neighbors1(b, node)
         return float(score / len(SigmaOutA))
     else:
         return 0

def common_neighbors3(a: str, b: str) -> float:
     score = 0
     SigmaInB = SigmaIn[b]
     if SigmaInB:
         for node in SigmaInB:
             score += common_neighbors1(a, node)
         return float(score / len(SigmaInB))
     else:
         return 0

def knn1(a:str, b:str) -> float:
    """
    knn1 = $w_{ab} = w_a^out$
    """
    return 1/math.sqrt(1+len(SigmaOut[a]))

def knn2(a:str, b:str) -> float:
    """
    knn2 = $w_{ab} = w_b^in$
    """
    return 1/math.sqrt(1+len(SigmaIn[b]))

def knn3(a:str, b:str) -> float:
    """
    knn3 = $w_{ab} = w_a^out  w_b^in$
    """
    return 1/math.sqrt(1+len(SigmaOut[a])) + 1/math.sqrt(1+len(SigmaIn[b]))

def knn4(a:str, b:str) -> float:
    """
    knn4 = $w_{ab} = w_a^out * w_b^in$
    """
    wAOut = 1/math.sqrt(1+len(SigmaOut[a]))
    wBIn = 1/math.sqrt(1+len(SigmaIn[b]))
    return  wAOut* wBIn

In [4]:
"""
Construct Train Data
Output:
1. train data: positive, negative
2. label of train data: train_label
"""

import random

train_dic = {}
for item in train_set:
    train_dic[item[0]] = item[1:]

# collect user list in the original train set
user_list = list(train_dic.keys())
random.seed(0)
# select 240 user randomly
user_train = random.sample(user_list, 240)
print("The user_train has been constructed.")

# construct positive dataset
    # the element of positive_list = the link that comes from traversing the adjacent list of one user
positive_list = set()
sink_set = set()
for user in user_train:
    for sink in train_dic[user]:
        if (user, sink) not in positive_list:
            positive_list.add((user, sink))
        sink_set.add(sink)
print("The length of positive list is", len(positive_list), ".\n")
print("The length of sink set is", len(sink_set), ".\n")

# construct negative dataset
    # the element (user1 -> user2) of negative_list = 
    # user1 = an element in the user list
    # user2 = any element except user1's adjacency
negative_list = set()

count=0
for user in user_train:
    for sink in sink_set:
        if (user, sink) not in positive_list:
            negative_list.add((user, sink))
    count=count+1
    if count%30==0:
        print(count)
print("The length of negative list is", len(negative_list), ".")

# construct train dataset
random.seed(0)
positive_train = random.sample(list(positive_list), 10000)
random.seed(0)
negative_train = random.sample(list(negative_list), 10000)
# create label for positive and negative train data
positive_label = [1] * len(positive_train)
negative_label = [0] * len(negative_train)
# combine positive and negative train data & label
#train_link = []
#train_link.extend(positive_train)
#train_link.extend(negative_train)
Y_train = []
Y_train.extend(positive_label)
Y_train.extend(negative_label)

del user_list, user_train
del positive_list, sink_set, negative_list, count
#del positive_train, negative_train, positive_label, negative_label

The user_train has been constructed.
The length of positive list is 196230 .

The length of sink set is 158792 .

30
60
90
120
150
180
210
240
The length of negative list is 37913850 .


In [5]:
"""
Get Feature
"""

def getFeature(pair:tuple) -> float:
    node1 = pair[0]
    node2 = pair[1]
    result = []
    result.append(adar1(node1,node2))
    #result.append(salton(node1,node2))
    #result.append(allocation(node1,node2))
    result.append(jaccard1(node1,node2))
    result.append(jaccard2(node1,node2))
    result.append(jaccard3(node1,node2))
    result.append(cosine1(node1,node2))
    result.append(cosine2(node1,node2))
    result.append(cosine3(node1,node2))
    #result.append(knn1(node1,node2))
    #result.append(knn2(node1,node2))
    #result.append(knn3(node1,node2))
    #result.append(knn4(node1,node2))
    #result.append(common_neighbors1(node1,node2))
    #result.append(common_neighbors2(node1,node2))
    #result.append(common_neighbors3(node1,node2))
    #result.append(AA(node1,node2))
    #result.append(CNPA(node1,node2))
    print(result)
    return result

In [8]:
"""

"""

import multiprocessing as mp
import time
    
if __name__ == '__main__':
         
    # construct the # of pools corresponding to the cpu_count in ur PC
    pool = mp.Pool(mp.cpu_count())
    
    startTime = time.time()
    
    positive = pool.map(getFeature, positive_train)
    pool.close()
    pool.join()
    
    endTime = time.time()
    print("Total time:" + (endTime - startTime).__str__())
    
    pool = mp.Pool(mp.cpu_count())
    
    startTime = time.time()
    
    negative = pool.map(getFeature, negative_train)
    pool.close()
    pool.join()
    
    endTime = time.time()
    print("Total time:" + (endTime - startTime).__str__())
    
    X_train = []
    X_train.extend(positive)
    X_train.extend(negative)

[0.7438495819329047, 0.003443526170798898, 0.06033433424285167, 0.08790911971587315, 0.00019303528685043626, 0.01470609558951014, 9.675157968452468e-05, 0.026379807127383248, 0.22941573387056174, 0.255795540997945, 0.006051942811492503, 5, 2.282033426183844, 183.0]
[0.11227035521868514, 0.00045004500450045, 0.08927637389429452, 0.08102409761794155, 1.4716270308453026e-05, 0.006410110112504182, 4.3866539887289446e-05, 0.021363815131845643, 0.17677669529663687, 0.19814051042848252, 0.0037766246379359572, 1, 6.571689497716895, 465.61290322580646]
[0, 0.0, 0.2223555691300555, 0.5024823069610225, 0.0, 0.181943475974961, 0.00015773323008976453, 0.01774992567234187, 0.5773502691896258, 0.5951001948619677, 0.01024792436502243, 0, 1.057674125433344, 1687.5]
[0, 0.0, 0.06848829213686185, 0.20376119576245708, 0.0, 0.03667702794708861, 0.00038162684696033415, 0.04389512813061471, 0.4082482904638631, 0.45214341859447776, 0.01792011101901568, 0, 1.106177606177606, 120.2]
[0.949875663262269, 0.044117

[7.729871047723311, 0.0019333250712603792, 0.031030769184651426, 0.02408684117236202, 6.173806911814292e-06, 0.001424135114632088, 2.434680703348698e-06, 0.004999000299900035, 0.0562543950463012, 0.061253395346201236, 0.0002812157377071548, 78, 13.423691115831563, 1713.3460317460317]
[8.263190478227209, 0.005017301038062283, 0.06078697708132282, 0.03614344283296494, 2.642709342068652e-05, 0.0027368463459473227, 3.944788680212763e-06, 0.007621605866236445, 0.07216878364870323, 0.07979038951493968, 0.0005500420248161054, 87, 19.085627977227837, 1723.4188481675392]
[2.944160202174995, 0.002141163875506615, 0.059211084294053314, 0.06786378712433999, 4.661119933945272e-05, 0.0041114282607244874, 1.0496353168213882e-05, 0.00875175052517506, 0.14586499149789456, 0.15461674202306963, 0.0012765740159463544, 28, 8.67644580620452, 2464.108695652174]
[0, 0.0, 0.6314171184457192, 1.0, 0.0, 0.6314171184457192, 0.00011634671320535195, 0.010785785934387398, 0.7071067811865475, 0.7178925671209349, 0.00

[0.33654782713963444, 0.0010107816711590297, 0.025991977681173607, 0.09403273741649171, 7.801529099703542e-05, 0.006647344786703437, 5.38016724252555e-05, 0.01855993633210361, 0.2672612419124244, 0.285821178244528, 0.004960351633933538, 3, 1.7898001378359751, 409.15384615384613]
[0, 0.0, 0.22363133094307008, 1.0, 0.0, 0.22363133094307008, 2.4932681759250024e-05, 0.004999000299900035, 0.7071067811865475, 0.7121057814864475, 0.0035348270112128995, 0, 1.0, 40108.0]
[0.21158784437649747, 4.986287708800798e-05, 0.1102659510840052, 0.2841743043334414, 1.2466340879625012e-05, 0.060283910130473045, 1.0261496681152768e-05, 0.004999000299900035, 0.4472135954999579, 0.45221259579985795, 0.0022356208980236626, 2, 1.1802823941022116, 11836.75]
[0.09731593463652254, 0.00033783783783783786, 0.04861030028190944, 0.3389956887731702, 0.0001126887536623845, 0.027371766935213485, 0.00011508507566322993, 0.01855993633210361, 0.5, 0.5185599363321036, 0.009279968166051806, 1, 1.1657477601654032, 1150.3333333

[0, 0.0, 0.15048831020715472, 0.5078323784466793, 0.0, 0.11288088512918101, 1.3073881994114006e-05, 0.004999000299900035, 0.5773502691896258, 0.5823492694895259, 0.002886174168826306, 0, 1.0224915656628764, 20506.5]
[3.1580059012080164, 0.0015641293013555788, 0.03216244722684283, 0.04179998938136337, 2.955639140543925e-05, 0.006496563928434737, 8.690562417436087e-06, 0.007621605866236445, 0.13608276348795434, 0.1437043693541908, 0.0010371691884934595, 27, 3.9433019635180666, 1283.811320754717]
[5.681138711071893, 0.003461605030865978, 0.057839606894534885, 0.040252623183031515, 2.2172522922693283e-05, 0.003090275485314001, 4.910672036224326e-06, 0.007621605866236445, 0.079555728417573, 0.08717733428380944, 0.0006063424064000878, 60, 16.236958289764146, 1783.8726114649683]
[10.086132539559149, 0.01944209636517329, 0.01914150713588974, 0.026794848521543974, 5.257218961645921e-05, 8.286587524720024e-05, 0.00013100223357996905, 0.049446817643414874, 0.042835293687811936, 0.0922821113312268

[2.8624973762780437, 0.0016235648846109243, 0.04665539499273393, 0.0613937826096176, 4.275018016147354e-05, 0.009356934431572126, 8.152503581682142e-06, 0.007621605866236445, 0.16012815380508713, 0.16774975967132358, 0.0012204336763904638, 28, 4.857615894039735, 2204.4473684210525]
[6.785536533377403, 0.005004619648906683, 0.06219606652604733, 0.03098658179136284, 2.0307740373349997e-05, 0.001885578158630854, 4.914876085510471e-06, 0.008972309321891575, 0.06311944030978031, 0.07209174963167189, 0.0005663271426840208, 65, 22.27928508171645, 1159.736]
[0.32860018580410644, 0.0011043622308117063, 0.07012974808734274, 0.05118700514808428, 5.044899606497831e-05, 0.014000815405085947, 1.4417616038207582e-05, 0.016708490237236185, 0.20851441405707477, 0.22522290429431097, 0.0034839610515956573, 4, 3.4708182072046916, 570.9545454545455]
[50.262393760211644, 0.06673662119622245, 0.01371462023522463, 0.03580794626605618, 6.069510785978743e-05, 0.0001683478548765969, 2.09360027025691e-05, 0.01712

...

[0.18303284812324394, 0.006557377049180328, 0.007889417511269706, 0.004807665832669555, 0.0011074197120708748, 0.001964310232569817, 2.4853007673224914e-05, 0.05783149319662402, 0.3779644730092272, 0.4357959662058512, 0.021858249849398707, 2, 0.697986577181208, 35.0]
[0.09068940734870236, 0.0041841004184100415, 0.004847844705861439, 0.0011414922239118275, 8.549931600547196e-05, 0.00019295495737390732, 7.111214596198096e-06, 0.07761505257063328, 0.1203858530857692, 0.1980009056564025, 0.00934375431601251, 1, 4.33939393939394, 11.147058823529411]
[0, 0.0, 0.002170884251310026, 0.0005093782670702103, 0.0, 4.073647300338199e-05, 4.779704695323342e-06, 0.12309149097933272, 0.07198157507486945, 0.19507306605420216, 0.008860319399006455, 0, 2.1384615384615384, 1.5677083333333333]
[0, 0.0, 0.010935690117551392, 0.002975221077402184, 0.0, 0.0025430692233702917, 2.5482924791675886e-06, 0.026379807127383248, 0.3779644730092272, 0.40434428013661045, 0.009970629898986465, 0, 0.3934540389972145, 95.

[0, 0.0, 0.01049611493161695, 0.0011386875859777637, 0.0, 0.00047114872803209805, 9.212543065543353e-06, 0.08111071056538127, 0.1259881576697424, 0.20709886823512366, 0.010218988991416095, 0, 4.52317880794702, 14.080645161290322]
[1.4708174935445752, 0.009467455621301775, 0.024144569033602785, 0.005859275152080531, 3.669649021006447e-05, 0.0004541744157163781, 7.107293613910651e-06, 0.026793191107712163, 0.05643326479831003, 0.08322645590602219, 0.0015120272485732462, 16, 16.152298850574713, 71.83386581469648]
[0, 0.0, 0.0007613553590702078, 4.359027909522446e-05, 0.0, 6.42052447358165e-05, 6.933816590537446e-07, 0.19611613513818404, 0.2672612419124244, 0.46337737705060844, 0.05241424183609592, 0, 0.6, 4.076923076923077]
[0, 0.0, 0.0, 0.0010570824524312897, 0.0, 0.0, 4.46026351236831e-06, 0.06788442333021306, 0.7071067811865475, 0.7749912045167605, 0.04800153607373193, 0, 0.0, 1.0]
[0, 0.0, 0.00012767731024484458, 5.28340197212648e-05, 0.0, 2.607724551020105e-05, 5.522250828534874e-07,

[0, 0.0, 0.015605526505651753, 0.0007843807892468519, 0.0, 0.001004145130563903, 3.363578131687945e-06, 0.0574484989621426, 0.2, 0.2574484989621426, 0.011489699792428521, 0, 2.251655629139073, 29.666666666666668]
[0.4761641535684693, 0.0007998400319936012, 0.0005597447179754584, 0.0009563315714957519, 2.61488155240288e-06, 2.4963725530417035e-06, 3.2335611331163406e-06, 0.0949157995752499, 0.0944911182523068, 0.1894069178275567, 0.008968700041677189, 4, 3.0454545454545454, 7.468468468468468]
[0.07383035914027619, 0.004975124378109453, 0.006934918348528131, 0.00015876430822394475, 0.0016750418760469012, 0.0034372574314258364, 8.008755558854676e-07, 0.07254762501100116, 0.5, 0.5725476250110012, 0.03627381250550058, 1, 0.3439153439153439, 24.333333333333332]
[0, 0.0, 1.5323791719022954e-05, 5.779010633379565e-05, 0.0, 1.5323791719022954e-05, 8.408420528654215e-07, 0.12126781251816648, 0.7071067811865475, 0.828374593704714, 0.08574929257125441, 0, 0.014925373134328358, 1.0]
[0, 0.0, 0.0, 0

[0.16078418297223057, 0.013888888888888888, 0.00858054652163834, 0.00037587891193413374, 0.000641025641025641, 0.0014356476156847549, 3.295669620249514e-06, 0.1, 0.19245008972987526, 0.2924500897298753, 0.01924500897298753, 2, 1.0808080808080809, 7.153846153846154]
[0, 0.0, 0.00024606299212598425, 0.0004974505658500186, 0.0, 0.00024606299212598425, 4.261996881923081e-06, 0.17407765595569785, 0.7071067811865475, 0.8811844371422453, 0.12309149097933274, 0, 0.03125, 20.0]
[0, 0.0, 0.00775441015913649, 0.000284520311138156, 0.0, 0.0005917774636408325, 1.5257038336326583e-06, 0.07124704998790965, 0.11624763874381928, 0.18749468873172892, 0.008282301328557356, 0, 1.5561224489795917, 5.575342465753424]
[0.14400740803123657, 0.0028089887640449437, 0.0009263721137429878, 0.006154942037866843, 3.2266391326794014e-05, 2.1548767275913755e-05, 5.917229528103478e-05, 0.07106690545187015, 0.2581988897471611, 0.32926579519903126, 0.018349396085439344, 1, 1.4060913705583757, 8.357142857142858]
[0, 0.0,

[0, 0.0, 0.0032971708805912808, 0.00041643771820911596, 0.0, 0.0005691868782339511, 4.834224838227648e-06, 0.10540925533894598, 0.21320071635561041, 0.3186099716945564, 0.022473328748774734, 0, 0.7640449438202247, 3.380952380952381]
[0.1811915216088903, 0.00975609756097561, 0.023161785788852737, 0.0006612576764082592, 0.00026595744680851064, 0.0007669570020581211, 4.173815509007006e-06, 0.09128709291752768, 0.14433756729740646, 0.23562466021493414, 0.013176156917368249, 2, 6.7899159663865545, 25.51063829787234]
[0.0881141788423624, 0.005681818181818182, 0.0016912241620058348, 2.1824657535770674e-05, 0.00030525030525030525, 2.3652721665551943e-05, 1.0422380492350205e-06, 0.22941573387056174, 0.07980868844676221, 0.30922442231732394, 0.018309368829260975, 1, 0.5555555555555556, 0.4423076923076923]
[0, 0.0, 0.0001522068967861686, 0.0007269100553716003, 0.0, 5.085232112163452e-05, 7.672882582832818e-06, 0.10259783520851541, 0.5, 0.6025978352085154, 0.051298917604257706, 0, 0.13829787234042

In [9]:
title = ["adar1", "jaccard1", "jaccard2", "jaccard3",
         "cosine1", "cosine2", "cosine3",
         "knn1", "knn2", "knn3", "knn4", 
        "common_neighbors1", "common_neighbors2", "common_neighbors3"]
test_pd = pd.DataFrame(columns = title, data = X_train)
test_pd.to_csv('/Users/dnhb/PycharmProjects/SML_Ass1/X_train3Score.csv',encoding='utf-8')

In [7]:
assert(len(X_train) == len(Y_train))

In [6]:
"""
This cell only works when reading data from local 
"""

# read X_train data
score_name = "X_train3Score.csv"
with open(os.path.join(file_dir, score_name)) as f:
    X_train = f.readlines()
    X_train = parse(X_train)
    X_train.pop(0)
    
for i in range(0, len(X_train)):
    X_train[i] = X_train[i][0].split(",")
    for j in range(0, 7):
        X_train[i][j] = float(X_train[i][j])
        

# construct Y
positive_label = [1] * 10000
negative_label = [0] * 10000
Y_train = []
Y_train.extend(positive_label)
Y_train.extend(negative_label)

"""
Step:
1. run this cell
2. run the *assert block*

if need to select feature, then
1. run the X_trian1 cell, select the features
2. edit and run *getFeature* cell
3. run the paparmeters of RF
4. gridsearch and so on 
"""

'\nStep:\n1. run this cell\n2. run the *assert block*\n\nif need to select feature, then\n1. run the X_trian1 cell, select the features\n2. edit and run *getFeature* cell\n3. run the paparmeters of RF\n4. gridsearch and so on \n'

In [7]:
# "adar1",  "jaccard2", "jaccard3", "cosine2", "cosine3"
X_train1 = []
for item in X_train:
    new = []
    new.extend(item[:7])
    #new.extend(item[2:4])
    #new.extend(item[5:])
    X_train1.append(new)
    
X_train = X_train1

In [34]:
"""
Train RandomForestClassifier
Using GridSearchCV to find the best estimators
"""

from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import GridSearchCV
import numpy as np

# Create the random grid for rfc
para_rfc = {'n_estimators': [50, 100],
                 "criterion": ["gini", "entropy"],
                 'max_depth': [50,70, None],
                 'min_samples_split': [2, 3, 5, 8, 10],
                 'min_samples_leaf': [1, 2, 4, 6, 8]}

rfc = RandomForestClassifier(bootstrap=True, criterion='gini',
           max_leaf_nodes=None,
           min_impurity_decrease=0.0, min_impurity_split=None,
           min_weight_fraction_leaf=0.0, n_jobs=1,
           oob_score=False, random_state=None, verbose=0, warm_start=False )
grid_rfc = GridSearchCV(estimator = rfc, param_grid = para_rfc, cv = 3, verbose=2, n_jobs = -1)
# Fit the random search model
grid_rfc.fit(X_train, Y_train)
model = grid_rfc.best_estimator_
model.fit(X_train, Y_train)
print (model)
print ("rfc train success!")

Fitting 3 folds for each of 300 candidates, totalling 900 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done  25 tasks      | elapsed:    8.2s
[Parallel(n_jobs=-1)]: Done 146 tasks      | elapsed:   46.1s
[Parallel(n_jobs=-1)]: Done 349 tasks      | elapsed:  2.0min
[Parallel(n_jobs=-1)]: Done 632 tasks      | elapsed:  3.6min
[Parallel(n_jobs=-1)]: Done 900 out of 900 | elapsed:  5.1min finished


RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                       criterion='entropy', max_depth=50, max_features='auto',
                       max_leaf_nodes=None, max_samples=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=5,
                       min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=1,
                       oob_score=False, random_state=None, verbose=0,
                       warm_start=False)
rfc train success!


In [8]:
"""
Best estimators of RFC with features adar1, jaccard 1-3, cos 1-3
"""

from sklearn.ensemble import RandomForestClassifier

model = RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                       criterion='entropy', max_depth=50, max_features='auto',
                       max_leaf_nodes=None, max_samples=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=5,
                       min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=1,
                       oob_score=False, random_state=None, verbose=0,
                       warm_start=False)
model.fit(X_train, Y_train)
print ("rfc train success!")

rfc train success!


In [ ]:
"""
Train Support Vector Classification
Using GridSearchCV to find the best estimators
"""

from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import GridSearchCV
import numpy as np

para_svc = {"C": [1, 3, 5],
               "kernel": ['linear', 'poly', 'rbf', 'sigmoid', 'precomputed']}

svc = RandomForestClassifier(bootstrap=True, criterion='gini',
           max_leaf_nodes=None,
           min_impurity_decrease=0.0, min_impurity_split=None,
           min_weight_fraction_leaf=0.0, n_jobs=1,
           oob_score=False, random_state=None, verbose=0, warm_start=False )
grid_svc = GridSearchCV(estimator = svc, param_grid = para_svc, cv = 3, verbose=2, n_jobs = -1)
# Fit the random search model
grid_svc.fit(X_train, Y_train)
model = grid_svc.best_estimator_
model.fit(X_train, Y_train)
print (model)
print ("svc train success!")

In [10]:
"""
Train LogisticRegression
Using GridSearchCV to find the best estimators
"""

from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV
import numpy as np

# Create the random grid for rfc
para_lgr = {'penalty': ["l1", "l2", "elasticnet", "none"],
                 'tol': [1e-4, 1e-6, 1e-8],
                 'C': [1, 3, 5],
                 'fit_intercept': [True, False],
                 'solver': ['newton-cg', 'lbfgs', 'liblinear', 'sag', 'saga'],
                 'max_iter': [100, 200],
                 'multi_class': ['auto'],
                 'n_jobs': [1]}    

lgr = LogisticRegression(random_state=0)
grid_lgr = GridSearchCV(estimator = lgr, param_grid = para_lgr, cv = 3, verbose=2, n_jobs = -1)
# Fit the random search model
grid_lgr.fit(X_train, Y_train)
model = grid_lgr.best_estimator_
model.fit(X_train, Y_train)
print (model)
print ("lgr train success!")

Fitting 3 folds for each of 720 candidates, totalling 2160 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done  25 tasks      | elapsed:   16.7s
[Parallel(n_jobs=-1)]: Done 146 tasks      | elapsed:   51.1s
[Parallel(n_jobs=-1)]: Done 349 tasks      | elapsed:  1.9min
[Parallel(n_jobs=-1)]: Done 632 tasks      | elapsed:  3.2min
[Parallel(n_jobs=-1)]: Done 997 tasks      | elapsed:  5.2min
[Parallel(n_jobs=-1)]: Done 1442 tasks      | elapsed:  7.4min
[Parallel(n_jobs=-1)]: Done 1969 tasks      | elapsed: 10.2min
[Parallel(n_jobs=-1)]: Done 2160 out of 2160 | elapsed: 11.1min finished


LogisticRegression(C=1, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None, max_iter=100,
                   multi_class='auto', n_jobs=1, penalty='none', random_state=0,
                   solver='newton-cg', tol=0.0001, verbose=0, warm_start=False)
lgr train success!


In [10]:
"""
Train LogisticRegression
Using GridSearchCV to find the best estimators
"""

from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV
import numpy as np

# Create the random grid for rfc
para_lgr = {'penalty': ["l1", "l2", "elasticnet", "none"],
                 'tol': [1e-4, 1e-6, 1e-8],
                 'C': [1, 3, 5],
                 'fit_intercept': [True, False],
                 'solver': ['newton-cg', 'lbfgs', 'liblinear', 'sag', 'saga'],
                 'max_iter': [100, 200],
                 'multi_class': ['auto'],
                 'n_jobs': [1]}    

lgr = LogisticRegression(random_state=0)
grid_lgr = GridSearchCV(estimator = lgr, param_grid = para_lgr, cv = 3, verbose=2, n_jobs = -1)
# Fit the random search model
grid_lgr.fit(X_train, Y_train)
model = grid_lgr.best_estimator_
model.fit(X_train, Y_train)
print (model)
print ("lgr train success!")

Fitting 3 folds for each of 720 candidates, totalling 2160 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done  25 tasks      | elapsed:   16.7s
[Parallel(n_jobs=-1)]: Done 146 tasks      | elapsed:   51.1s
[Parallel(n_jobs=-1)]: Done 349 tasks      | elapsed:  1.9min
[Parallel(n_jobs=-1)]: Done 632 tasks      | elapsed:  3.2min
[Parallel(n_jobs=-1)]: Done 997 tasks      | elapsed:  5.2min
[Parallel(n_jobs=-1)]: Done 1442 tasks      | elapsed:  7.4min
[Parallel(n_jobs=-1)]: Done 1969 tasks      | elapsed: 10.2min
[Parallel(n_jobs=-1)]: Done 2160 out of 2160 | elapsed: 11.1min finished


LogisticRegression(C=1, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None, max_iter=100,
                   multi_class='auto', n_jobs=1, penalty='none', random_state=0,
                   solver='newton-cg', tol=0.0001, verbose=0, warm_start=False)
lgr train success!


In [10]:
"""
Train LogisticRegression
Using GridSearchCV to find the best estimators
"""

from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV
import numpy as np

# Create the random grid for rfc
para_lgr = {'penalty': ["l1", "l2", "elasticnet", "none"],
                 'tol': [1e-4, 1e-6, 1e-8],
                 'C': [1, 3, 5],
                 'fit_intercept': [True, False],
                 'solver': ['newton-cg', 'lbfgs', 'liblinear', 'sag', 'saga'],
                 'max_iter': [100, 200],
                 'multi_class': ['auto'],
                 'n_jobs': [1]}    

lgr = LogisticRegression(random_state=0)
grid_lgr = GridSearchCV(estimator = lgr, param_grid = para_lgr, cv = 3, verbose=2, n_jobs = -1)
# Fit the random search model
grid_lgr.fit(X_train, Y_train)
model = grid_lgr.best_estimator_
model.fit(X_train, Y_train)
print (model)
print ("lgr train success!")

Fitting 3 folds for each of 720 candidates, totalling 2160 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done  25 tasks      | elapsed:   16.7s
[Parallel(n_jobs=-1)]: Done 146 tasks      | elapsed:   51.1s
[Parallel(n_jobs=-1)]: Done 349 tasks      | elapsed:  1.9min
[Parallel(n_jobs=-1)]: Done 632 tasks      | elapsed:  3.2min
[Parallel(n_jobs=-1)]: Done 997 tasks      | elapsed:  5.2min
[Parallel(n_jobs=-1)]: Done 1442 tasks      | elapsed:  7.4min
[Parallel(n_jobs=-1)]: Done 1969 tasks      | elapsed: 10.2min
[Parallel(n_jobs=-1)]: Done 2160 out of 2160 | elapsed: 11.1min finished


LogisticRegression(C=1, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None, max_iter=100,
                   multi_class='auto', n_jobs=1, penalty='none', random_state=0,
                   solver='newton-cg', tol=0.0001, verbose=0, warm_start=False)
lgr train success!


In [ ]:
"""
Best estimators of LGR with features adar1, jaccard 1-3, cos 1-3
"""

from sklearn.linear_model import LogisticRegression

model = LogisticRegression(C=1, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None, max_iter=100,
                   multi_class='auto', n_jobs=1, penalty='none', random_state=0,
                   solver='newton-cg', tol=0.0001, verbose=0, warm_start=False)
model.fit(X_train, Y_train)

In [ ]:
import multiprocessing as mp
import time

if __name__ == '__main__':
    
    def getPro(record:list) -> list:
        feature = getFeature((record[1], record[-1]))
        prediction = model.predict_proba([feature])[0][1]
        label = model.predict([feature])[0]
        pro = [record[0], prediction, label]
        print(pro)
        return pro
    
    # construct the # of pools corresponding to the cpu_count in ur PC
    pool = mp.Pool(mp.cpu_count())
    
    startTime = time.time()
    
    result = pool.map(getPro, test_set)
    pool.close()
    pool.join()
    
    endTime = time.time()
    print("Total time:" + (endTime - startTime).__str__())
    
    title = ["Id", "Predicted", "Label"]
    test_pd = pd.DataFrame(columns = title, data = result)
    test_pd.to_csv('/Users/dnhb/PycharmProjects/SML_Ass1/LGR2.csv',encoding='utf-8')

[0, 0.0, 0.0006682103297357281, 1.8060941139843826e-05, 0.0, 0.00034322807471536454, 7.228122423328354e-08]
[0.21933342447606208, 0.005154639175257732, 0.0010560980236248875, 0.00576653084902314, 0.001038961038961039, 0.0002158649279589648, 1.5493731237062647e-05]
[442, 0.005175631580022181, 0]
[316, 2.2395450644157276e-05, 0]
[0, 0.0, 0.004756335876775657, 0.0005961701829318617, 0.0, 0.0011086098198699584, 3.067381859917711e-05]
[1, 0.015090638751595177, 0]
[0, 0.0, 0.0004547391940738875, 0.007885478256716273, 0.0, 5.10988236771775e-05, 0.0002286423081153753]
[2, 0.36522157168539976, 0]
[0.822336943717954, 0.02147239263803681, 0.01244905313913601, 0.006981832564143511, 0.0004018369690011481, 0.0005297209380207124, 3.7517070022812676e-05]
[127, 0.022624407758992795, 0]
[0.4627293341056383, 0.011152416356877323, 0.006910701545848951, 0.024294678294895095, 0.0006920415224913495, 0.0005541850751437438, 0.00018663650315648496]
[3, 0.133358511940644, 0]
[0, 0.0, 0.0, 5.02373715807189e-05, 0

[257, 0.005056213755415817, 0]
[1.4992748812047982, 0.06578947368421052, 0.05428443917729768, 0.04243421989789361, 0.003246753246753247, 0.004320262850029424, 0.00044262996812483973]
[383, 0.018121363090060235, 0]
[3.592771144497777, 0.047058823529411764, 0.026487611459291485, 0.016931379656897366, 0.0009388018541336619, 0.0006132863004908547, 0.0003408795834033138]
[454, 0.9290631396492709, 1]
[29.89794923735107, 0.18254764292878636, 0.04679525197987243, 0.06124789248925164, 0.000530893943725242, 0.0008230413547663114, 0.0002354258927378303]
[258, 0.9999999999999687, 1]
[0, 0.0, 0.0007490310165941996, 0.0006286491974390266, 0.0, 9.222095759689695e-05, 5.8356978613035805e-06]
[259, 0.005626415950181049, 0]
[0, 0.0, 0.0051606380063914815, 0.0002720222470984673, 0.0, 0.000513008629464267, 4.529348676903707e-06]
[324, 0.007588974190530877, 0]
[0, 0.0, 0.0, 1.2793569670069464e-05, 0.0, 0.0, 1.421860570666575e-06]
[0, 0.0, 6.905600441958428e-05, 0.00035469531338881303, 0.0, 1.38150169233957

[267, 0.08239199010115397, 0]
[0.07383035914027619, 0.00014938751120406333, 0.006384472566084606, 0.007378505642107187, 7.470491558344539e-05, 0.0035315754336635377, 3.950294492876662e-06]
[140, 0.04944039226940077, 0]
[0.5172961569809289, 0.004721435316336166, 0.02029835066061346, 0.007664649744812133, 0.00031776294884016526, 0.002724675445812265, 2.3513796954190744e-05]
[387, 0.031249689636740994, 0]
[0, 0.0, 0.00019913457713614886, 1.9235023130115314e-05, 0.0, 6.720287486824699e-05, 4.478559122130755e-07]
[141, 0.004547388588411043, 0]
[0, 0.0, 0.011337564732222773, 0.001167309945543843, 0.0, 0.0006269754528367193, 5.7439213904946165e-06]
[461, 0.01226423335263008, 0]
[0, 0.0, 0.0003287983662890618, 0.00010565494715320857, 0.0, 0.00016671936964153948, 3.4633627961208005e-07]
[268, 0.004821630162486722, 0]
[0.13855321617185712, 0.006993006993006993, 0.02590677769342888, 0.013859465015711687, 0.0017857142857142857, 0.01088549009255951, 0.00010351906049609279]
[142, 0.00059574836232763

[27, 0.004728790195851201, 0]
[0.8060768890162648, 0.011128775834658187, 0.011176205205873221, 0.001360302166243377, 8.211336336336337e-05, 0.00012430374347677586, 7.772420850567822e-06]
[79, 0.0186868801161406, 0]
[0, 0.0, 0.01042244105204916, 0.0019911437140306934, 0.0, 0.003951149009502896, 6.563869713462504e-06]
[80, 0.05168427684072338, 0]
[0, 0.0, 0.0, 2.1830459797995477e-05, 0.0, 0.0, 1.3909744920006604e-07]
[81, 0.004363093744375602, 0]
[11.206011323326726, 0.03492884864165589, 0.016500024527156015, 0.017019706703737734, 5.730736059984534e-05, 0.00015036458044052783, 4.831619959880819e-05]
[339, 0.9933319203822609, 1]
[0, 0.0, 0.0016357918034605973, 0.0010131108316079904, 0.0, 0.00013103458211019846, 6.46992446775721e-06]
[82, 0.006371938140683945, 0]
[21.32274735057269, 0.05430646835005189, 0.01833074187676214, 0.040487477810314615, 7.259860462707437e-05, 0.0001010053482594864, 4.6768541783360535e-05]
[196, 0.9999987429721808, 1]
[0.9497483271394277, 0.018612521150592216, 0.03

[398, 0.9928046614425232, 1]
[5.083882847816846, 0.037037037037037035, 0.06790412892824028, 0.012475455640145978, 0.00010228669781165478, 0.00048780892293389283, 1.9084323902181933e-05]
[32, 0.9822212717624286, 1]
[0, 0.0, 0.0001617061359459462, 9.717228646390049e-05, 0.0, 0.0001617061359459462, 1.1772716275940024e-07]
[158, 0.004751895048768668, 0]
[0, 0.0, 0.013672603881223657, 6.47332988089073e-05, 0.0, 0.013672603881223657, 7.041763289718663e-07]
[159, 0.7100455680055286, 1]
[0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[474, 0.004339109982655435, 0]
[0, 0.0, 0.0041356938535295085, 1.0736119539749122e-05, 0.0, 0.0005196308620709307, 4.2954739124265185e-07]
[33, 0.006545022257267414, 0]
[0.4910568663541155, 0.008021390374331552, 0.03811630281525538, 0.07037104244429566, 0.0016129032258064516, 0.012497395030551481, 0.00037130247549140634]
[160, 0.9996754250470526, 1]
[0, 0.0, 0.012534016304814896, 0.0011061972911174409, 0.0, 0.0002316608040517131, 1.0706219711677241e-05]
[34, 0.01178782286200446

...

[1172, 0.007511128027286597, 0]
[1.0226200276348212, 0.01951219512195122, 0.01666591229641659, 0.016841967497307677, 0.00018602488082781072, 0.00028420055332816207, 0.00010699291673278496]
[935, 0.5762571431500358, 1]
[0.0864303862565374, 0.0021551724137931034, 0.009319083259771732, 0.01322462519144251, 0.00014814814814814815, 0.0009017447132482767, 4.035923279218937e-05]
[1173, 0.05816320911444028, 0]
[0.21746067507328515, 0.0056179775280898875, 0.005083655260426649, 0.010703075070702386, 0.00024024024024024023, 0.0002887518997268099, 4.064813841892971e-05]
[936, 0.019422514214411553, 0]
[0.3086147226207659, 0.007537688442211055, 0.037665081621898605, 0.003946244556482129, 0.00024703557312252963, 0.002190541936321585, 1.1957332869236836e-05]
[882, 0.047599954201730944, 0]
[1.4426950408889634, 0.043478260869565216, 0.0, 0.0, 0.0078125, 0.0, 0.0]
[1261, 2.6885549040630514e-24, 0]
[0, 0.0, 0.02032946718738551, 0.025112179706197044, 0.0, 0.0010603469593585197, 0.0002402798561189174]
[1262

[1325, 0.004735658155410037, 0]
[0, 0.0, 0.00014287297233393263, 0.0022652907123080794, 0.0, 0.00014287297233393263, 2.3972964888396526e-06]
[1185, 0.006779734464283609, 0]
[2.4991260391984813, 0.06451612903225806, 0.027414514874029672, 0.014527082976110184, 0.0009648435144425014, 0.0011394176049361656, 0.0002165978495507227]
[1186, 0.7783228741645425, 1]
[2.9612858711285313, 0.1875, 0.11709165988018658, 0.041644143687681975, 0.005247376311844078, 0.00417321006452555, 0.0005939160218627479]
[1187, 0.07051554533556563, 0]
[5.085712469432119, 0.03388189738625363, 0.019290736670277676, 0.011434962221629687, 0.00019857480029048658, 0.00022240942096092862, 8.063468513643591e-05]
[1272, 0.8343189001342888, 1]
[1.4951154530003798, 0.01807909604519774, 0.04366634924969178, 0.007604692646524713, 0.00012226994146326552, 0.0006650285640942025, 1.342323469384493e-05]
[376, 0.3297392541101409, 0]
[0.08641664237211644, 0.004807692307692308, 0.005423041259765856, 0.0002458302432572667, 0.000131337010

[0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[1279, 0.004339109982655435, 0]
[1.7884723047616267, 0.02051983584131327, 0.02833376957925111, 0.018909364054555542, 0.00011077632045373981, 0.00034856898623637317, 6.76394531440323e-05]
[1005, 0.8038991154678081, 1]
[1.0076617189463062, 0.009458297506448839, 0.042236937157425866, 0.005214209426149483, 0.00030100700525394046, 0.001977316345185357, 4.849716782127694e-06]
[1337, 0.05923444351420023, 0]
[0, 0.0, 0.0034686313501267672, 0.0002639573624549102, 0.0, 0.0002524389601170807, 1.133422957478478e-05]
[1450, 0.007020676145108805, 0]
[0.13202089627872077, 0.002320185614849188, 0.003666703162572746, 0.0012839909589809312, 6.105006105006105e-05, 0.00019216394375386919, 3.850964634316449e-06]
[1280, 0.005943789885232938, 0]
[2.2242081839022765, 0.003892644949805368, 0.00365133702645605, 0.015130196869349844, 4.7870710784313725e-06, 1.8060594395956574e-05, 3.9040478200775675e-05]
[1387, 0.21717742928969266, 0]
[0, 0.0, 0.001410324311548632, 2.73892905614

[1123, 0.021330317019948912, 0]
[0.5173192003379169, 0.007547169811320755, 0.02249937941057663, 0.004722901746951817, 0.00038412291933418694, 0.0015226072361613117, 6.332042854812408e-06]
[1069, 0.008273211563726464, 0]
[0, 0.0, 0.0051883480572763865, 0.003114886176389116, 0.0, 9.23608809181358e-05, 6.440149231721023e-05]
[1344, 0.025059421522069216, 0]
[0, 0.0, 2.8717264657294103e-05, 0.004965689842091526, 0.0, 1.436702138889326e-05, 1.369450854312094e-05]
[1124, 0.011487364348722108, 0]
[0, 0.0, 0.004663362138391224, 3.205152863634563e-05, 0.0, 7.821332874845935e-05, 4.0200842849631205e-06]
[1287, 0.0059312179388604025, 0]
[0.575538344550899, 0.0026595744680851063, 0.008220141901499394, 0.0035906400544185187, 9.364611134522639e-06, 8.77551238462528e-05, 1.856824586395309e-05]
[1399, 0.021087798628907545, 0]
[0, 0.0, 0.01696554452024863, 4.035501653210511e-05, 0.0, 0.01696554452024863, 8.968505299938207e-07]
[1400, 0.9179449893158941, 1]
[0, 0.0, 0.007630733827184293, 0.00195268736336

[1294, 0.0047828119740660644, 0]
[0.15361129482611352, 0.004784688995215311, 0.0023650205290301853, 0.00019007475891842887, 0.0023923444976076554, 0.0012226627428489258, 4.550682234518332e-07]
[1459, 1.2608137504966027e-09, 0]
[0, 0.0, 5.005361372307249e-05, 8.259474570348486e-05, 0.0, 5.005361372307249e-05, 2.325144151783121e-07]
[1357, 0.0045125562988930544, 0]
[0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[1358, 0.004339109982655435, 0]
[0.5064830614962788, 0.009478672985781991, 0.021822366116026365, 0.024003314821849888, 0.0008051529790660225, 0.0024426462016011374, 6.648706824451926e-05]
[1295, 0.03774331948899669, 0]
[0, 0.0, 0.0038917969224143496, 0.0001256829941079423, 0.0, 0.0011935678491828518, 5.894268860900909e-07]
[1296, 0.008720841664426706, 0]
[0.08673271802933455, 0.006134969325153374, 0.005639454113690315, 0.0004364729103795691, 0.000333000333000333, 0.00036112325750947124, 3.0649966700041245e-06]
[1359, 0.001280781821181959, 0]
[0, 0.0, 0.0, 1.8820155875199625e-05, 0.0, 0.0, 2.37